In [ ]:
# @title Introduction
# @markdown We use ES/GA algorithms to optimize a neural network for the MNIST classification task.

# Numpy is all you need ;)
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import cm
from IPython.display import clear_output
from sklearn import datasets
import warnings
warnings.filterwarnings('ignore')

In [ ]:
# @title Data Inspection
# @markdown We download the MNIST dataset from `sklearn.datasets`, the images are of size (8, 8).

images, labels = datasets.load_digits(return_X_y=True)
print(f'#samples={len(images)}, image_size={labels.shape}')


seed = 42               # @param
num_images_per_row = 5  # @param
np_random = np.random.RandomState(seed=seed)

fig, axes = plt.subplots(num_images_per_row, num_images_per_row, figsize=(8, 8))
indices = np_random.randint(
    low=0, high=len(images), size=(num_images_per_row, num_images_per_row))
for i in range(num_images_per_row):
    for j in range(num_images_per_row):
        ax = axes[i][j]
        ix = indices[i][j]
        ax.imshow(images[ix].reshape([8, 8]), cmap=plt.cm.gray)
        ax.set_axis_off()
        ax.set_title(f'label={labels[ix]}')
plt.tight_layout()

In [ ]:
# @title Split data for training
# @markdown We divide evenly the dataset into training and valdiation and test splits. \\
# @markdown The histgram below shows the splits are well balanced.

data_size = len(images)
assert data_size % 3 == 0, 'Dataset cannot be evenly divided into 3 splits'
split_size = data_size // 3

indices = np.arange(data_size)
np_random.shuffle(indices)
train_ix = indices[:split_size]
train_images, train_labels = images[train_ix], labels[train_ix]
valid_ix = indices[split_size:-split_size]
valid_images, valid_labels = images[valid_ix], labels[valid_ix]
test_ix = indices[-split_size:]
test_images, test_labels = images[test_ix], labels[test_ix]

fig, axes = plt.subplots(1, 3, figsize=(8, 3), sharex=True, sharey=True)
for i, (split_labels, split_name) in enumerate(
    zip([train_labels, valid_labels, test_labels], ['train', 'valid', 'test'])):
    ax = axes[i]
    ax.hist(split_labels)
    ax.set_title(f'split={split_name}')
plt.tight_layout()

In [ ]:
# @title Neural network definition
# @markdown For simplicity, we will use a feedforward neural network (a.k.a MLP) to do the classification task. \\
# @markdown The code in this cell defines the network.

from typing import List, Optional


NAME_TO_FUNC = {
    'tanh': lambda x: np.tanh(x),
    'sigmoid': lambda x: 1 / (1 + np.exp(-x)),
    'relu': lambda x: np.maximum(0, x),
}


def softmax(x, axis=-1):
    e_x = np.exp(x - np.max(x, axis=axis, keepdims=True))
    return e_x / e_x.sum(axis=axis, keepdims=True)


class MLP(object):
    """A feedforward neural network."""

    def __init__(self,
                 input_dim: int,
                 output_dim: int,
                 act_fn: str,
                 hidden_dims: List[int]):
        """Initialization.

        Arguments:
          input_dim     - Input dimension. 64 in our MNIST example.
          output_dim    - Output dimension. 10 in our MNIST example.
          act_fn        - Activation function. See NAME_TO_FUNC above.
          hidden_dims   - Hidden dimension. E.g., [32, 32].
        """
        self.input_dim = input_dim
        self.output_dim = output_dim
        self.act_fn = NAME_TO_FUNC[act_fn]
        self.w_sizes, self.b_sizes = [], []
        self.num_params = 0

        # Paramter sizes for the hidden layers.
        dim_in = input_dim
        for hidden_dim in hidden_dims:
            self.w_sizes.append((dim_in, hidden_dim))
            self.b_sizes.append(hidden_dim)
            self.num_params += dim_in * hidden_dim + hidden_dim
            dim_in = hidden_dim

        # Parameters for the output layer.
        self.w_sizes.append((dim_in, output_dim))
        self.b_sizes.append(output_dim)
        self.num_params += dim_in * output_dim + output_dim
        print(f'#params={self.num_params}')

    def __call__(self,
                 params: np.ndarray,
                 data: np.ndarray,
                 labels: Optional[np.ndarray],
                 use_acc: bool=True):
        """This is a batch forward function.

        Arguments:
          params    - Network parameters of shape (M,), where M
                      is the parameters' size.
          data      - Network input data of shape (N, input_dim), where N
                      is the data batch size.
          lables    - Ground truth labels of shape (N,), where N is the
                      data batch size.
          use_acc   - If true we use accuracy as loss, cross-entropy otherwise.

        Returns:
          If labels are not none, we return logits of shape (N, output_dim);
          If labels are None, we return fitness scores:
            accuracy if use_acc is true,
            negative x-entropy loss otherwise.
        """
        assert params.size == self.num_params, 'Inconsistent params sizes.'

        x = data / np.max(data, axis=-1, keepdims=True)  # Make x in [0, 1]
        offset = 0
        for w_size, b_size in zip(self.w_sizes, self.b_sizes):
            ss = offset
            ee = ss + np.prod(w_size)
            w = params[ss:ee].reshape(w_size)
            ss = ee
            ee = ss + b_size
            b = params[ss:ee]
            x = np.einsum('bi,ij->bj', x, w) + b[None, ...]
            offset = ee
            if offset != params.size:
                x = self.act_fn(x)
        assert offset == params.size

        if labels is None:
            return x
        else:
            if use_acc:
                preds = np.argmax(x, axis=-1)
                return np.mean(preds == labels)
            else:
                one_hot = np.zeros((len(labels), self.output_dim))
                one_hot[np.arange(len(labels)), labels.astype(int)] = 1
                probs = softmax(x, axis=-1)
                return np.sum(one_hot * np.log(probs + 1e-9)) / x.shape[0]


hidden_dims = [32, 32]  # @param
act_fn = 'tanh'         # @param
model = MLP(input_dim=64, output_dim=10, hidden_dims=hidden_dims, act_fn=act_fn)
rand_params = np_random.randn(model.num_params) * 0.01
accuracy = model(rand_params, train_images, train_labels, use_acc=True)
neg_loss = model(rand_params, train_images, train_labels, use_acc=False)
print('Test with random parameters on the training split:')
print(f'accuracy={accuracy}')
print(f'neg_loss={neg_loss}')

In [ ]:
# @title Train with CMA-ES

try:
    import cma
except ModuleNotFoundError:
    !pip install cma
    clear_output()
    import cma


# @markdown Feel free to play with the following parameters.
num_gen = 150            # @param
pop_size = 256          # @param
init_stdev = 0.5       # @param
acc_as_fitness = True   # @param
test_interval = 10      # @param


def eval_func(params):
    return -model(params, train_images, train_labels, use_acc=acc_as_fitness)


# Initialize the CMA-ES solver.
algo = cma.CMAEvolutionStrategy(
    x0=np.zeros(model.num_params),
    sigma0=init_stdev,
    inopts={
        "popsize": pop_size,
        "seed": seed,
        "randn": np.random.randn,
    }
)

# Optimization loop, all expressions are self-explained.
best = []
best_valid_ix = -1
best_valid_acc = 0.
for i in range(num_gen):
    population = algo.ask()
    fitness_scores = list(map(eval_func, np.array(population)))
    # In tell(), CMA-ES accepts population in addition to fitness scores.
    algo.tell(population, fitness_scores)
    ix = np.argmin(fitness_scores)
    best.append((population[ix], fitness_scores[ix]))
    if (i + 1) % test_interval == 0:
        valid_acc = model(best[-1][0], valid_images, valid_labels, True)
        if valid_acc > best_valid_acc:
            best_valid_acc = valid_acc
            best_valid_ix = i
        metric = 'acc' if acc_as_fitness else 'loss'
        print(
            f"Gen={i+1}, {metric}@train={-best[-1][1]}, acc@valid={valid_acc}")

# Evaluation on the test split.
test_acc = model(best[best_valid_ix][0], test_images, test_labels, True)
print(f'acc@test={test_acc}')

In [ ]:
# @title Train with your ES/GA implementation
# @markdown Although we didn't tune its hyper-parameters, CMA-ES may not be the best ES algorithm for this problem.  \\
# @markdown Can you implement other ES/GA algorithms to beat the baseline established by CMA-ES?  \\
# @markdown Implement the `MyAlgo` class and run the test code in this cell to take on the challenge! \\

# @markdown `MyAlgo` should maintain some internal state/distribution, from which `ask()` samples the next generation and `tell()` updates it based on the fitness.

from typing import Union


class MyAlgo(object):
    """Your should implement this class with the ask() and tell() interfaces."""

    def __init__(self,
                 pop_size,
                 num_params,
                 init_x,
                 stdev,
                 seed):
        """Initialize the internal states.

        Arguments:
          pop_size - Population size.
          num_params - Number of parameters to optimize.
          init_x - Initial guess of the solution.
          stdev - Standard deviation used for population sampling.
          seed - Random seed.
        """
        # Your code here

    def ask(self) -> np.ndarray:
        """Return a population of solutions for the next generation.

        Returns:
          An array of size (pop_size, num_params).
        """
        # Your code here

    def tell(self, fitness: Union[np.ndarray, List]) -> None:
        """Update the internal state based on the fitness scores.

        Arguments:
          fitness - An array of size pop_size, representing the fitness score
                    for each of the individual in the population.
        """
        # Your code here


# === Test below ===

num_gen = 150            # @param
pop_size = 256          # @param
init_stdev = 0.5       # @param
acc_as_fitness = True   # @param
test_interval = 10      # @param

algo = MyAlgo(
    pop_size=pop_size,
    num_params=model.num_params,
    init_x=np.zeros(model.num_params),
    stdev=init_stdev,
)

best = []
best_valid_ix = -1
best_valid_acc = 0.
for i in range(num_gen):
    population = algo.ask()
    fitness_scores = list(map(eval_func, np.array(population)))
    algo.tell(fitness_scores)
    ix = np.argmin(fitness_scores)
    best.append((population[ix], fitness_scores[ix]))
    if (i + 1) % test_interval == 0:
        valid_acc = model(best[-1][0], valid_images, valid_labels, True)
        if valid_acc > best_valid_acc:
            best_valid_acc = valid_acc
            best_valid_ix = i
        metric = 'acc' if acc_as_fitness else 'loss'
        print(f"Gen={i+1}, {metric}@train={-best[-1][1]}, acc@valid={valid_acc}")

# Evaluation on the test split.
test_acc = model(best[best_valid_ix][0], test_images, test_labels, True)
print(f'acc@test={test_acc}')

# How about a differen type of neural network?

With ES/GA, we don't have to restrict ourselves to conventional networks and how they are normally set up.
For exmaple, assuming we have a neural network with a bank of random weights, instead of modifying these weights, can we optimize a combination of the weights and/or choose a subset of the weights such that they allow the neural network to perform well on a task?

## Exercise Task: Implement `MyNN` in the next cell

**Objective:** In this exercise, you are required to implement a neural network that structurally resembles a Multi-Layer Perceptron (MLP), but incorporates a unique architectural twist.

### Architecture Differences:
- **Traditional MLP Layers**: Typically defined with weight parameters of shape $(D_\text{in}, D_\text{out})$.
- **MyNN Layers**: Each layer's parameters are three-dimensional with a shape $(N, D_\text{in}, D_\text{out})$, where:
  - $N$ is the number of parameter sets per layer
  - $D_\text{in}$ is the dimensionality of the input
  - $D_\text{out}$ is the dimensionality of the output

### Key Implementation Details:
1. **Parameter Initialization**: Initialize these parameters randomly at the start and *keep them unchanged* throughout the training process.

2. **Forward Pass Behavior**:
   - The network transforms its complex parameter structure into the conventional two-dimensional format $(D_\text{in}, D_\text{out})$ used in standard MLPs during the forward pass.
   - **Condensing Method**: This transformation varies between layers:
     - **Input and Output Layers**: Create a linear combination of the $N$ sets of weights to form a single $(D_\text{in}, D_\text{out})$ matrix.
     - **Hidden Layers**: Select one from the $N$ available sets to use as the MLP weights for that layer.

### Task Instructions:
- **Step 1**: Define the network architecture with the specified parameter shapes for each layer.
- **Step 2**: Implement the method for condensing weights from $(N, D_\text{in}, D_\text{out})$ to $(D_\text{in}, D_\text{out})$. Ensure different methods for input, output, and hidden layers as described.
- **Step 3**: Code the forward pass using the condensed weights for typical MLP operations, such as matrix multiplication followed by an activation function.

This task will enhance your skills in tensor operations and in implementing custom neural network architectures. It also explores innovative approaches to modifying traditional neural network models that can be useful in scenarios such as [model merging](https://arxiv.org/abs/2403.13187).


In [ ]:
# @title Implement the unconventional neural network `MyNN`

class MyNN(object):
    """An unconventional neural network."""

    def __init__(self,
                 input_dim: int,
                 output_dim: int,
                 hidden_dim: int,
                 num_hidden_layers: int):
        # Your code here

    def __call__(self,
                 params: np.ndarray,
                 data: np.ndarray,
                 labels: np.ndarray,
                 use_acc: bool):
        """This is a batch forward function.

        Arguments:
          params    - Network parameters of shape (M,), where M
                      is the parameters' size.
          data      - Network input data of shape (N, input_dim), where N
                      is the data batch size.
          lables    - Ground truth labels of shape (N,), where N is the
                      data batch size.
          use_acc   - If true we use accuracy as loss, cross-entropy otherwise.

        Returns:
          Accuracy if use_acc is true, negative x-entropy loss otherwise.
        """
        # Your code here


num_hidden_layers = 2  # @param
hidden_dim = 32  # @param
model = MyNN(
    input_dim=64,
    output_dim=10,
    hidden_dim=hidden_dim,
    num_hidden_layers=num_hidden_layers,
)
rand_params = np_random.randn(model.num_params) * 0.01
accuracy = model(rand_params, train_images, train_labels, use_acc=True)
neg_loss = model(rand_params, train_images, train_labels, use_acc=False)
print('Test with random parameters on the training split:')
print(f'accuracy={accuracy}')
print(f'neg_loss={neg_loss}')

In [ ]:
# @title Train `MyNN` with CMA-ES

# @markdown Feel free to play with the following parameters.
num_gen = 600            # @param
pop_size = 256          # @param
init_stdev = 0.5       # @param
acc_as_fitness = True   # @param
test_interval = 30      # @param


def eval_func(params):
    return -model(params, train_images, train_labels, use_acc=acc_as_fitness)


# Initialize the CMA-ES solver.
algo = cma.CMAEvolutionStrategy(
    x0=np.zeros(model.num_params),
    sigma0=init_stdev,
    inopts={
        "popsize": pop_size,
        "seed": seed,
        "randn": np.random.randn,
    }
)

# Optimization loop, all expressions are self-explained.
best = []
best_valid_ix = -1
best_valid_acc = 0.
for i in range(num_gen):
    population = algo.ask()
    fitness_scores = list(map(eval_func, np.array(population)))
    # In tell(), CMA-ES accepts population in addition to fitness scores.
    algo.tell(population, fitness_scores)
    ix = np.argmin(fitness_scores)
    best.append((population[ix], fitness_scores[ix]))
    if (i + 1) % test_interval == 0:
        valid_acc = model(best[-1][0], valid_images, valid_labels, True)
        if valid_acc > best_valid_acc:
            best_valid_acc = valid_acc
            best_valid_ix = i
        metric = 'acc' if acc_as_fitness else 'loss'
        print(
            f"Gen={i+1}, {metric}@train={-best[-1][1]}, acc@valid={valid_acc}")

# Evaluation on the test split.
test_acc = model(best[best_valid_ix][0], test_images, test_labels, True)
print(f'acc@test={test_acc}')